In [2]:

import os
import time
import shutil
import nighres
import numpy
import nibabel
from PIL import Image
from scipy.signal import convolve2d
import glob
# import math
from nighres.io import load_volume, save_volume
# import scipy.ndimage
# from nibabel import processing
# import subprocess



# code by @pilou, using nighres; adapted, modularized, and extended by @csteele

# file parameters
subject = 'zefir'
# inputdir = '/path/to/input/dir/'
# prefix = '_Image_'
# suffix = '.vsi - 20x'
# format = '.tif'
output_dir = '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/'
zfill_num = 4
per_slice_template = True #use a median of the slice and adjacent slices to create a slice-specific template for anchoring the registration
run_syn = True #include some nonlinear reg in the initial regs as well (best to do this with hand-created slice data)
rescale=20

all_image_fnames = ['/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_01_-_20x_02_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_02_-_20x_01_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_02_-_20x_02_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_03_-_20x_01_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_03_-_20x_02_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_04_-_20x_01_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_04_-_20x_02_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_05_-_20x_01_cellCount_29_downsample_10p002um_pix.tif', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/TP1/_Image_05_-_20x_02_cellCount_29_downsample_10p002um_pix.tif']

In [191]:
all_image_names = [os.path.basename(image).split('.')[0] for image in all_image_fnames][0:7] #remove the .tif extension to comply with formatting below


if not os.path.exists(output_dir):
     os.makedirs(output_dir)


def coreg_multislice(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[-1,-2,-3], 
                     zfill_num=4, input_source_file_tag='coreg0nl', reg_level_tag='coreg1nl',run_syn=True,
                     run_rigid=True,previous_target_tag=None,scaling_factor=64,image_weights=None):
    ''' Co-register to slices before/after
    target_offset_list: negative values indicate slices prior to the current, positive after
    '''
    all_image_names = [os.path.basename(image_fname).split('.')[0] for image_fname in all_image_fnames]

    if type(template) is list: #we have a list of templates, one for each slice
        per_slice_template = True
    else:
        per_slice_template = False
        targets = [template]
    for idx,img in enumerate(all_image_fnames):
        img = os.path.basename(img).split('.')[0]
        # current image
        previous_tail = f'_{input_source_file_tag}_ants-def0.nii.gz'
        nifti = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+previous_tail

        sources = [nifti]
        image_weights_ordered = [image_weights[0]]
        if per_slice_template:
            targets = [template[idx]]
        if previous_target_tag is not None:
            tail = f'_{previous_target_tag}_ants-def0.nii.gz' #if we want to use the previous iteration rather than building from scratch every time (useful for windowing)
        else:
            tail = f'_{reg_level_tag}_ants-def0.nii.gz'
        # append additional images as additional targets to stabilize reg
        for idx2,slice_offset in enumerate(target_slice_offet_list):
            if slice_offset < 0: #we add registration targets for the slices that came before
                if idx > numpy.abs(slice_offset + 1):        
                    prev1 = output_dir+subject+'_'+str(idx+slice_offset).zfill(zfill_num)+'_'+all_image_names[idx+slice_offset]+tail
                    sources.append(nifti)
                    targets.append(prev1)
                    image_weights_ordered.append(image_weights[idx2+1]) #since we have already added the first image weight
            elif slice_offset > 0: #we add registration targets for the slices that come afterwards
                 if idx < len(all_image_fnames)-1*slice_offset:
                    prev1 = output_dir+subject+'_'+str(idx+slice_offset).zfill(zfill_num)+'_'+all_image_names[idx+slice_offset]+tail
                    sources.append(nifti)
                    targets.append(prev1)
                    image_weights_ordered.append(image_weights[idx2+1])
        
        output = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+"_"+reg_level_tag
        print(sources)
        print(targets)
        print(image_weights_ordered)
        print(f'output: {output.split("/")[-1]}')
        coreg_output = nighres.registration.embedded_antspy_2d_multi(source_images=sources, 
                        target_images=targets,
                        image_weights=image_weights_ordered,
                        run_rigid=run_rigid,
                        rigid_iterations=1000,
                        run_affine=False,
                        run_syn=run_syn,
                        coarse_iterations=2000,
                        medium_iterations=1000, fine_iterations=200,
        			    scaling_factor=scaling_factor,
                        cost_function='MutualInformation',
                        interpolation='Linear',
                        regularization='High',
                        convergence=1e-6,
                        mask_zero=False,
                        ignore_affine=True, ignore_orient=True, ignore_res=True,
                        save_data=True, overwrite=False,
                        file_name=output)
        time.sleep(1) #to avoid overloading the system
        
        # cleanup extra deformation files produced after registration (def? are all the same as def0 - the deformed image)
        def_files = glob.glob(f'{output}_ants-def*')
        for f in def_files:
            if 'def0' in f:
                pass
            else:
                os.remove(f)
                time.sleep(.5)

def coreg_multislice_reverse(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[1,2,3], 
                             zfill_num=4, input_source_file_tag='coreg1nl', reg_level_tag='coreg2nl',run_syn=True,
                             run_rigid=True, previous_target_tag=None,scaling_factor=64,image_weights=None):
    ''' Co-register to slices before/after
    target_offset_list: negative values indicate slices prior to the current, positive after
    differs in that we reverse the list (and the idx) and the offsets are the opposite sign
    TODO: can likely be combined with standard, with some more thought.
    '''
    all_image_names = [os.path.basename(image_fname).split('.')[0] for image_fname in all_image_fnames]
    
    if type(template) is list: #we have a list of templates, one for each slice
        per_slice_template = True
    else:
        per_slice_template = False
        targets = [template]
    for idx,img in reversed(list(enumerate(all_image_fnames))):
        img = os.path.basename(img).split('.')[0]
        # current image
        previous_tail = f'_{input_source_file_tag}_ants-def0.nii.gz'
        nifti = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+previous_tail

        sources = [nifti]
        image_weights_ordered = [image_weights[0]]
        if per_slice_template:
            targets = [template[idx]]
        if previous_target_tag is not None:
            tail = f'_{previous_target_tag}_ants-def0.nii.gz' #if we want to use the previous iteration rather than building from scratch every time (useful for windowing)
        else:
            tail = f'_{reg_level_tag}_ants-def0.nii.gz'

        # append additional images as additional targets to stabilize reg
        for idx2, slice_offset in enumerate(target_slice_offet_list):
            if slice_offset < 0: #we add registration targets for the slices that came before
                if idx > numpy.abs(slice_offset + 1):        
                    prev1 = output_dir+subject+'_'+str(idx+slice_offset).zfill(zfill_num)+'_'+all_image_names[idx+slice_offset]+tail
                    sources.append(nifti)
                    targets.append(prev1)
                    image_weights_ordered.append(image_weights[idx2+1]) #add 1 b/c we have already added the first image weight above
            elif slice_offset > 0: #we add registration targets for the slices that come afterwards
                 if idx < len(all_image_fnames)-1*slice_offset:
                    prev1 = output_dir+subject+'_'+str(idx+slice_offset).zfill(zfill_num)+'_'+all_image_names[idx+slice_offset]+tail
                    sources.append(nifti)
                    targets.append(prev1)
                    image_weights_ordered.append(image_weights[idx2+1])
        
        output = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+"_"+reg_level_tag
        print(sources)
        print(targets)
        print(image_weights_ordered)
        print(f'output: {output.split("/")[-1]}')
        coreg_output = nighres.registration.embedded_antspy_2d_multi(source_images=sources, 
                        target_images=targets,
                        image_weights=image_weights_ordered,
                        run_rigid=run_rigid,
                        rigid_iterations=1000,
                        run_affine=False,
                        run_syn=run_syn,
                        coarse_iterations=2000,
                        medium_iterations=1000, fine_iterations=200,
					    scaling_factor=scaling_factor,
                        cost_function='MutualInformation',
                        interpolation='Linear',
                        regularization='High',
                        convergence=1e-6,
                        mask_zero=False,
                        ignore_affine=True, ignore_orient=True, ignore_res=True,
                        save_data=True, overwrite=False,
                        file_name=output)
        time.sleep(1) #to avoid overloading the system
        # cleanup extra deformation files produced after registration (def? are all the same as def0 - the deformed image)
        def_files = glob.glob(f'{output}_ants-def*')
        for f in def_files:
            if 'def0' in f:
                pass
            else:
                os.remove(f)
                time.sleep(.5)

def generate_stack_and_template(output_dir,subject,all_image_fnames,zfill_num=4,reg_level_tag='coreg12nl',
                                per_slice_template=False,missing_idxs_to_fill=None):
    #we can also output a per_slice_template based on the median of the current and neighbouring slices
    stack = []
    stack_tail = f'_{reg_level_tag}_stack.nii.gz'
    img_stack = output_dir+subject+stack_tail
    template_tail = f'_{reg_level_tag}_template.nii.gz'
    template = output_dir+subject+template_tail

    template_list = []

    img_tail = f'_{reg_level_tag}_ants-def0.nii.gz'
    # if (os.path.isfile(img_stack)):
    if False:
        print('Stacking was already completed for this level: {}'.format(template))
    else:
        #this can only handle if there is a single missing slice between two good slices
        #and that they are not at the start or end of the stack (or it will crash)
        for idx,img_name in enumerate(all_image_fnames):
            img_name = os.path.basename(img_name).split('.')[0]
            reg = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+img_tail
            stack.append(nighres.io.load_volume(reg).get_fdata())

        img = numpy.stack(stack,axis=-1)

        missing_idxs_to_fill = None #XXX SETTING TO NONE FOR TESTING TODO
        #now we fill any missing data with the mean of the neighbouring slices
        if missing_idxs_to_fill is not None and len(missing_idxs_to_fill)>0:
            missing_idxs_to_fill.sort() #sort it
            missing_slices_interpolated = []
            missing_idxs_pre = numpy.array(missing_idxs_to_fill)-1
            missing_idxs_post = numpy.array(missing_idxs_to_fill)+1
            
            for idx,img_idx in enumerate(missing_idxs_pre):
                img_name = all_image_fnames[img_idx]
                img_name = os.path.basename(img_name).split('.')[0]
                reg = output_dir+subject+'_'+str(img_idx).zfill(zfill_num)+'_'+img_name+img_tail
                _t = nighres.io.load_volume(reg).get_fdata()
                if idx==0:
                    pre_d = numpy.zeros(_t.shape+(len(missing_idxs_to_fill),))
                pre_d[...,idx] = _t

            for idx,img_idx in enumerate(missing_idxs_post):
                img_name = all_image_fnames[img_idx]
                img_name = os.path.basename(img_name).split('.')[0]
                reg = output_dir+subject+'_'+str(img_idx).zfill(zfill_num)+'_'+img_name+img_tail
                _t = nighres.io.load_volume(reg).get_fdata()
                if idx==0:
                    post_d = numpy.zeros(_t.shape+(len(missing_idxs_to_fill),))
                post_d[...,idx] = _t
            
            missing_slices_interpolated = .5*(pre_d+post_d)

            #now we can fill the slices with the interpolated value
            for idx,missing_idx in enumerate(missing_idxs_to_fill):
                print(idx)
                print(missing_idx)
                print(numpy.shape(missing_slices_interpolated))
                print(numpy.shape(img))
                img[...,missing_idx] = missing_slices_interpolated[...,idx]

        header = nibabel.Nifti1Header()
        header.set_data_shape(img.shape)
        
        nifti = nibabel.Nifti1Image(img,affine=None,header=header)
        save_volume(img_stack,nifti)

        if per_slice_template:
            num_slices = img.shape[-1]
            for idx,img_name in enumerate(all_image_fnames):
                img_name = os.path.basename(img_name).split('.')[0]
                slice_template_fname = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+template_tail
                if idx == 0: #if at the front, take the first two only
                    slice_template = numpy.median(img[...,0:2],axis=-1)
                elif idx == num_slices-1: #if at the end, take the last two only
                    slice_template = numpy.median(img[...,-2:],axis=-1)
                else: #take one on each side and the current slice
                    start = idx-1
                    stop = idx+2
                    slice_template = numpy.median(img[...,start:stop],axis=-1)

                header.set_data_shape(slice_template.shape)
                nifti = nibabel.Nifti1Image(slice_template,affine=None,header=header)
                nifti.update_header()
                save_volume(slice_template_fname,nifti)
                template_list.append(slice_template_fname)            

        img = numpy.median(img,axis=2)
        nifti = nibabel.Nifti1Image(img,affine=None,header=header)
        save_volume(template,nifti)
        print('Stacking: done - {}'.format(template))
    if per_slice_template:
        return template_list
    else:
        return template


In [192]:
def generate_gaussian_weights(slice_order_idxs, gauss_std=3):
    """
    Generates Gaussian weights for the given slice indices, ensuring the weights sum to 1.
    This should be agnostic to the order in which the slice_order_indices are input.
    
    Parameters:
    - slice_order_idxs: list of slice indices to generate weights for.
    - gauss_std: Standard deviation of the Gaussian distribution, controls the spread of the weights.
    
    Returns:
    - out_weights: Array of Gaussian weights corresponding to the input slice indices, summing to 1.
    """
    import numpy as np
    from scipy import signal

    # Ensure slice_order_idxs is a numpy array
    slice_order_idxs = np.array(slice_order_idxs)
    
    # Insert 0 into the beginning of the slice_order_idxs if it is not already there
    if 0 not in slice_order_idxs:
        slice_order_idxs = np.insert(slice_order_idxs,0,0) #insert 0 at the beginning
    if slice_order_idxs[0] != 0:
        print("0 must be the first element of slice_order_idxs")
        print("FIX THIS")
        return "0 must be the first emelement of slice_order_idxs"
    elif np.sum(slice_order_idxs==0)>1:
        print("There are multiple 0s in slice_order_idxs")
        print("FIX THIS")
        return "There are multiple 0s in slice_order_idxs"
    
    # Define the range of indices to cover both positive and negative slices symmetrically
    max_idx = np.max(np.abs(slice_order_idxs))
    num_vals = max_idx * 2 + 1  # Total number of values in the symmetric Gaussian
    
    # Generate a symmetric Gaussian, centered at 0
    gaussian_window = signal.windows.gaussian(num_vals, std=gauss_std)
    
    # Extract the weights corresponding to the absolute slice indices
    out_weights = np.zeros(slice_order_idxs.shape)
    
    for i, slice_idx in enumerate(slice_order_idxs):
        # Use the absolute value of the slice index to get the corresponding weight
        out_weights[i] = gaussian_window[max_idx + slice_idx]
    
    # Normalize the weights to sum to 1
    return out_weights / out_weights.sum()

In [182]:
def select_best_reg_by_MI(output_dir,subject,all_image_fnames,template_tag='coreg0nl',
                          zfill_num=zfill_num,reg_level_tag1='coreg1nl', reg_level_tag2='coreg2nl',reg_output_tag='coreg12nl',per_slice_template=False,
                          overwrite=True):
    '''
    Use MI to determine best registration (forwards or backwards) and select going forward
    reg_output_tag identifies the best registration outputs
    '''
    template_tail = f'_{template_tag}_template.nii.gz'
    out_tail = f'_{reg_output_tag}'
    tag1_tail = f'_{reg_level_tag1}'
    tag2_tail = f'_{reg_level_tag2}'
    
    for idx,img_name in enumerate(all_image_fnames):
        img_name = os.path.basename(img_name).split('.')[0]

        if not per_slice_template:
            template = output_dir+subject+template_tail #we use the generally defined template
        output = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+out_tail+'_ants-def0.nii.gz'
        if (not os.path.isfile(output)) or overwrite:
            if per_slice_template: #or,we use individual templates
                template = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+template_tail
            slice1 = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+tag1_tail+'_ants-def0.nii.gz'
            slice2 = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+tag2_tail+'_ants-def0.nii.gz'
        
            curr1 = nighres.io.load_volume(slice1).get_fdata()
            curr2 = nighres.io.load_volume(slice2).get_fdata()
            curr = nighres.io.load_volume(template).get_fdata()
            
            p1,v1 = numpy.histogram(curr1.flatten(), bins=100, density=True)
            p2,v2 = numpy.histogram(curr2.flatten(), bins=100, density=True)
            pc,vc = numpy.histogram(curr.flatten(), bins=100, density=True)

            # normalize histograms to 1
            p1 = p1/numpy.sum(p1)
            p2 = p2/numpy.sum(p2)
            pc = pc/numpy.sum(pc)
            
            p1c,v1,vc = numpy.histogram2d(curr1.flatten(), curr.flatten(), bins=100, density=True)
            p2c,v2,vc = numpy.histogram2d(curr2.flatten(), curr.flatten(), bins=100, density=True)
        
            # normalize joint histograms to 1
            p1c = p1c / numpy.sum(p1c)
            p2c = p2c / numpy.sum(p2c)
            
            p1pc = numpy.outer(p1,pc)
            p2pc = numpy.outer(p2,pc)
                
            mi1c = numpy.sum(p1c*numpy.log(p1c/(p1pc),where=(p1c*p1pc>0)))
            mi2c = numpy.sum(p2c*numpy.log(p2c/(p2pc),where=(p2c*p2pc>0)))
        
            print("MI: "+str(mi1c)+", "+str(mi2c))
            
            # copy the best result
            mapping= output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+out_tail+'_ants-map.nii.gz'
            inverse= output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+out_tail+'_ants-invmap.nii.gz'
            if (mi1c>mi2c): 
                mapping1= output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+tag1_tail+'_ants-map.nii.gz'
                inverse1= output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+tag1_tail+'_ants-invmap.nii.gz'
                shutil.copyfile(mapping1, mapping)
                shutil.copyfile(inverse1, inverse)
                shutil.copyfile(slice1, output)
            else:
                mapping2= output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+tag2_tail+'_ants-map.nii.gz'
                inverse2= output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+tag2_tail+'_ants-invmap.nii.gz'
                shutil.copyfile(mapping2, mapping)
                shutil.copyfile(inverse2, inverse)
                shutil.copyfile(slice2, output)

            # cleanup files, removing old mappings that are no longer needed
            map_files = glob.glob(output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img_name+"*"+'_ants-*map.nii.gz')
            for f in map_files:
                if out_tail in f:
                    pass
                else:
                    os.remove(f)
                    time.sleep(.5)

            os.remove(slice1)
            time.sleep(.5)
            os.remove(slice2)
            time.sleep(.5)

            

In [183]:
# 0. Convert to nifti
print('0. Converting images to .nii.gz')
for idx,img_orig in enumerate(all_image_fnames):
    img = os.path.basename(img_orig).split('.')[0] 
    output = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+'.nii.gz'
    
    if (os.path.isfile(output)):
        print('\t - already done, using existing image')
        nifti = output
    else:
        print('\t - image '+str(img_orig))
        # get the TIFF image
        slice_name = str(img_orig)
        if os.path.isfile(slice_name):
            slice_img = Image.open(slice_name)
            
            slice_img = numpy.array(slice_img)
            
            # crop: use various options
            image = slice_img
            slice_li = numpy.pad(image,pad_width=((0,rescale),(0,rescale)),mode='edge')
            
            ## alternative using 2d convolution to preserve cell counts (meaning is still the same here)
            kernel = numpy.ones((rescale,rescale)) #2d convolution kernel, all 1s
            slice_img = convolve2d(image,kernel,mode='full')[::rescale,::rescale] #can divide by rescale if we want the mean, otherwise sum is good (total cell count)

            #exceptions that need fixing, since rigid reg does not seem to address big flips
            if 'TP1' in img_orig: #we have files named the same within the subdirs, so we must specify specifically 
                if 'Image_11_-_20x_01_cellCount' in img_orig:
                    slice_img = numpy.flip(slice_img,axis=0) #flip x
            
            header = nibabel.Nifti1Header()
            header.set_data_shape(slice_img.shape)
            
            affine = numpy.eye(4)
            affine[0,3] = -slice_img.shape[0]/2.0
            affine[1,3] = -slice_img.shape[1]/2.0
                  
            nifti = nibabel.Nifti1Image(slice_img,affine=affine,header=header)
            save_volume(output,nifti)
                 
        else:
            print('\tfile '+slice_name+' not found')
            

0. Converting images to .nii.gz
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image
	 - already done, using existing image


In [184]:
# 1. Find largeest image as baseline
print('2. Identifying the largest image to set image size')
largest = -1
size= 0
for idx,img in enumerate(all_image_fnames):
    img = os.path.basename(img).split('.')[0]
    nifti = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+'.nii.gz'
    shape = nighres.io.load_volume(nifti).header.get_data_shape()
    
    if shape[0]*shape[1]>size:
        size = shape[0]*shape[1]
        largest = idx
        
template = output_dir+subject+'_'+str(largest).zfill(zfill_num)+'_'+os.path.basename(all_image_fnames[largest]).split('.')[0]+'.nii.gz'    

print(f"\tUsing the following image as the template for size: {template}")


2. Identifying the largest image to set image size
	Using the following image as the template for size: /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0006__Image_04_-_20x_01_cellCount_29_downsample_10p002um_pix.nii.gz


In [185]:
print('3. Bring all image slices into same place as our 2d template with an initial translation registration')
# initial step to bring all images into the same space of our 2d template
for idx,img in enumerate(all_image_fnames):
    img = os.path.basename(img).split('.')[0]
    nifti = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+'.nii.gz'

    sources = [nifti]
    targets = [template]
        
    output = output_dir+subject+'_'+str(idx).zfill(zfill_num)+'_'+img+'_coreg0nl.nii.gz'
    coreg1nl = nighres.registration.embedded_antspy_2d_multi(source_images=sources, 
                    target_images=targets,
                    run_rigid=False,
                    run_affine=False,
                    run_syn=False,
                    scaling_factor=16,
                    cost_function='MutualInformation',
                    interpolation='Linear',
                    regularization='High',
                    convergence=1e-6,
                    mask_zero=False,
                    ignore_affine=False, ignore_orient=False, ignore_res=False,
                    save_data=True, overwrite=False,
                    file_name=output)

template = generate_stack_and_template(output_dir,subject,all_image_fnames,zfill_num=4,reg_level_tag='coreg0nl',
                                       missing_idxs_to_fill=None)

#we keep all of the mappings, since they are small and we can use them to project data into the same space later (by concatenating!)
# map_invmap_fnames = glob.glob(os.path.join(output_dir,'*map*.gz'))
# for f in map_invmap_fnames:
#     os.remove(f) #cleanup map and inv-map produced by the registration, which we do not need


3. Bring all image slices into same place as our 2d template with an initial translation registration

Embedded ANTs Registration 2D Multi-contrasts

Outputs will be saved to /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg0nl_tmp_srccoordX.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg0nl_tmp_srccoordY.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg0nl_tmp_trgcoordX.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_coun

In [194]:
template

['/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_win12_rigsyn_4_template.nii.gz',
 '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0001__Image_01_-_20x_02_cellCount_29_downsample_10p002um_pix_coreg12nl_win12_rigsyn_4_template.nii.gz',
 '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0002__Image_02_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_win12_rigsyn_4_template.nii.gz',
 '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0003__Image_02_-_20x_02_cellCount_29_downsample_10p002um_pix_coreg12nl_win12_rigsyn_4_template.nii.gz',
 '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/

In [ ]:
print('4. Begin STAGE1 registration iterations')
# STEP 1: Rigid + Syn
num_reg_iterations = 5
run_rigid = True
run_syn = True
template_tag = 'coreg0nl' #initial template tag, which we update with each loop

missing_idxs_to_fill = None #[32,59,120,160,189,228] #these are the slice indices with missing or terrible data, fill with mean of neigbours
for iter in range(num_reg_iterations): #here we always go back to the original coreg0 images, just refining our target template
    iter_tag = f"_rigsyn_{iter}"
    print(f'\t iteration tag: {iter_tag}')
    if (iter == 0):
        first_run_slice_template = False
        run_syn = False
    else:
        first_run_slice_template = per_slice_template
        run_syn = True

    slice_offset_list_forward = [-1,-2,-3]
    slice_offset_list_reverse = [1,2,3]
    image_weights = generate_gaussian_weights([0,1,2,3]) #symmetric gaussian, so the same on both sides
    coreg_multislice(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[-1,-2,-3], 
                    zfill_num=zfill_num, input_source_file_tag='coreg0nl', reg_level_tag='coreg1nl'+iter_tag,run_syn=run_syn,scaling_factor=16,
                    image_weights=image_weights,run_rigid=run_rigid) 
    coreg_multislice_reverse(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[1,2,3], 
                            zfill_num=zfill_num, input_source_file_tag='coreg0nl', reg_level_tag='coreg2nl'+iter_tag,run_syn=run_syn,scaling_factor=16,
                            image_weights=image_weights,run_rigid=run_rigid)
    
    print(iter)
    print(template_tag)
    print(first_run_slice_template)
    select_best_reg_by_MI(output_dir,subject,all_image_fnames,template_tag=template_tag,
                        zfill_num=zfill_num,reg_level_tag1='coreg1nl'+iter_tag, reg_level_tag2='coreg2nl'+iter_tag,
                        reg_output_tag='coreg12nl'+iter_tag,per_slice_template=first_run_slice_template) #use the per slice templates after the first round, if requested
    template = generate_stack_and_template(output_dir,subject,all_image_fnames,
                                        zfill_num=4,reg_level_tag='coreg12nl'+iter_tag,per_slice_template=per_slice_template,
                                        missing_idxs_to_fill=missing_idxs_to_fill)
    template_tag = 'coreg12nl'+iter_tag
    
    

In [188]:
print('4. Begin STAGE1 registration iterations')
# STEP 1: Rigid + Syn
num_reg_iterations = 5
run_rigid = True
run_syn = True
template_tag = 'coreg0nl' #initial template tag, which we update with each loop

missing_idxs_to_fill = None #[32,59,120,160,189,228] #these are the slice indices with missing or terrible data, fill with mean of neigbours
for iter in range(num_reg_iterations): #here we always go back to the original coreg0 images, just refining our target template
    iter_tag = f"_rigsyn_{iter}"
    print(f'\t iteration tag: {iter_tag}')
    if (iter == 0):
        first_run_slice_template = False
        run_syn = False
    else:
        first_run_slice_template = per_slice_template
        run_syn = True

    slice_offset_list_forward = [-1,-2,-3]
    slice_offset_list_reverse = [1,2,3]
    image_weights = generate_gaussian_weights([0,1,2,3]) #symmetric gaussian, so the same on both sides
    coreg_multislice(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[-1,-2,-3], 
                    zfill_num=zfill_num, input_source_file_tag='coreg0nl', reg_level_tag='coreg1nl'+iter_tag,run_syn=run_syn,scaling_factor=16,
                    image_weights=image_weights,run_rigid=run_rigid) 
    coreg_multislice_reverse(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[1,2,3], 
                            zfill_num=zfill_num, input_source_file_tag='coreg0nl', reg_level_tag='coreg2nl'+iter_tag,run_syn=run_syn,scaling_factor=16,
                            image_weights=image_weights,run_rigid=run_rigid)
    
    print(iter)
    print(template_tag)
    print(first_run_slice_template)
    select_best_reg_by_MI(output_dir,subject,all_image_fnames,template_tag=template_tag,
                        zfill_num=zfill_num,reg_level_tag1='coreg1nl'+iter_tag, reg_level_tag2='coreg2nl'+iter_tag,
                        reg_output_tag='coreg12nl'+iter_tag,per_slice_template=first_run_slice_template) #use the per slice templates after the first round, if requested
    template = generate_stack_and_template(output_dir,subject,all_image_fnames,
                                        zfill_num=4,reg_level_tag='coreg12nl'+iter_tag,per_slice_template=per_slice_template,
                                        missing_idxs_to_fill=missing_idxs_to_fill)
    template_tag = 'coreg12nl'+iter_tag
    
    

4. Begin STAGE1 registration iterations
	 iteration tag: _rigsyn_0
['/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg0nl_ants-def0.nii.gz']
['/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_rigsyn_1_template.nii.gz']
[0.29822014479938147]
output: zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg1nl_rigsyn_0

Embedded ANTs Registration 2D Multi-contrasts

Outputs will be saved to /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg1nl_rigsyn_0_tmp_srci

/tmp/ipykernel_10806/2050979900.py:48: RuntimeWarning:

invalid value encountered in divide

/tmp/ipykernel_10806/2050979900.py:49: RuntimeWarning:

invalid value encountered in divide



MI: 0.7343778252252793, 0.7463509089213854
MI: 0.9001630616368073, 0.899991420714001
MI: 0.9644235319729972, 0.951043297073338
MI: 0.9323756364456006, 0.9346245010301608
MI: 1.0090157068262056, 1.0166577636983547
MI: 0.9433483575044689, 0.9825201920565217
MI: 0.9858889690274606, 0.9859153974524547
MI: 0.9030751438991872, 0.9074411748589447
MI: 0.9481071170609134, 0.9502538431406258

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_coreg12nl_rigsyn_0_stack.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_rigsyn_0_template.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0001__Image_01_-_20x_02_cellCount_29_downsample_10p002um_pix_coreg12nl_rigsyn_0_template.nii.gz

Saving /data/data_

In [189]:
generate_gaussian_weights([0,1,2,3])

array([0.29822014, 0.28210417, 0.23879602, 0.18087966])

In [190]:
first_run_slice_template = per_slice_template
run_syn = True
run_rigid = False
num_reg_iterations = 5
for iter in range(num_reg_iterations): #here we always go back to the original coreg0 images, just refining our target template
    iter_tag = f"_rigsyn_{iter}"
    print(f'\t iteration tag: {iter_tag}')

    image_weights = generate_gaussian_weights([0,3,2,1,1])
    coreg_multislice(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[-3,-2,-1,1], 
                    zfill_num=zfill_num, input_source_file_tag='coreg0nl', 
                    previous_target_tag = 'coreg12nl'+iter_tag,reg_level_tag='coreg12nl_win1'+iter_tag,run_syn=run_syn,
                    run_rigid=run_rigid,image_weights=image_weights) 
    image_weights = generate_gaussian_weights([0,1,1,2,3])
    coreg_multislice_reverse(output_dir,subject,all_image_fnames,template,target_slice_offet_list=[-1,1,2,3], 
                    zfill_num=zfill_num, input_source_file_tag='coreg0nl', 
                    previous_target_tag = 'coreg12nl'+iter_tag,reg_level_tag='coreg12nl_win2'+iter_tag,run_syn=run_syn,
                    run_rigid=run_rigid,image_weights=image_weights)
    
    select_best_reg_by_MI(output_dir,subject,all_image_fnames,template_tag=template_tag,
                        zfill_num=zfill_num,reg_level_tag1='coreg12nl_win1'+iter_tag, reg_level_tag2='coreg12nl_win2'+iter_tag,
                        reg_output_tag='coreg12nl_win12'+iter_tag,per_slice_template=per_slice_template)
    template = generate_stack_and_template(output_dir,subject,all_image_fnames,
                                        zfill_num=4,reg_level_tag='coreg12nl_win12'+iter_tag,per_slice_template=per_slice_template,
                                        missing_idxs_to_fill=missing_idxs_to_fill)
    template_tag = 'coreg12nl_win12'+iter_tag
    
final_reg_level_tag = 'coreg12nl_win12'+iter_tag
step1_iter_tag = iter_tag

	 iteration tag: _rigsyn_0
['/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg0nl_ants-def0.nii.gz', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg0nl_ants-def0.nii.gz']
['/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_rigsyn_9_template.nii.gz', '/data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0001__Image_01_-_20x_02_cellCount_29_downsample_10p002um_pix_coreg12nl_rigsyn_0_ants-def0.nii.gz']
[0.23260211753919144, 0.22003217557396257]
output: zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_

/tmp/ipykernel_10806/2050979900.py:48: RuntimeWarning:

invalid value encountered in divide

/tmp/ipykernel_10806/2050979900.py:49: RuntimeWarning:

invalid value encountered in divide



MI: 0.9989781336145404, 1.011942056588797
MI: 1.1968939679522042, 1.2018375528339376
MI: 1.2529851886555636, 1.2723502673333391
MI: 1.4805689820197667, 1.4711117892661019
MI: 1.1638522079811862, 1.1145657090587124
MI: 1.5001357406810463, 1.4773670108194767
MI: 1.335534667881339, 1.3291392128784882
MI: 1.5604646620581388, 1.5914276925507331
MI: 1.4454801640017405, 1.4561179668894935
MI: 1.6722740009962318, 1.704227813924559

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_coreg12nl_win12_rigsyn_0_stack.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0000__Image_01_-_20x_01_cellCount_29_downsample_10p002um_pix_coreg12nl_win12_rigsyn_0_template.nii.gz

Saving /data/data_drive/Macaque_CB/processing/results_from_cell_counts/slice_reg_perSliceTemplate_image_weights_TEST/zefir_0001__Image_01_-_20x_02_cellCount_29_downsample_10p002um_pix_